In [1]:
# 일반 패키지 설치
# !pip install pyupbit web3 ta yfinance scikit-learn pandas numpy matplotlib


In [1]:
import tensorflow as tf

gpus = tf.config.list_physical_devices('GPU')
if gpus:
    try:
        for gpu in gpus:
            tf.config.experimental.set_memory_growth(gpu, True)
        print(f"사용 가능한 GPU: {gpus}")
    except RuntimeError as e:
        print(e)
else:
    print("GPU를 찾을 수 없습니다.")

2025-09-18 21:28:55.452721: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


사용 가능한 GPU: [PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]


In [2]:
import pandas as pd
import numpy as np
import yfinance as yf
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_percentage_error, r2_score
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv1D, MaxPooling1D, Bidirectional, LSTM, Dense, Dropout
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping
import matplotlib.pyplot as plt
import datetime

# --- 1. 데이터 획득  ---
def get_ethereum_data(start_date="2020-01-01", end_date="2025-09-17", ticker="ETH-USD"):
    """
    Yahoo Finance에서 이더리움 일일 종가 데이터를 다운로드합니다.
    """
    print(f"이더리움 데이터 다운로드 중: {start_date} ~ {end_date}")
    try:
        data = yf.download(ticker, start=start_date, end=end_date)
        if data.empty:
            raise ValueError("다운로드된 데이터가 없습니다. 날짜 범위 또는 티커를 확인하세요.")
        df_close = data[['Close']]
        print("데이터 다운로드 완료.")
        return df_close
    except Exception as e:
        print(f"데이터 다운로드 중 오류 발생: {e}")
        return pd.DataFrame()

# --- 2. 데이터 전처리 ---
def preprocess_data(df, timesteps=16, train_ratio=0.7, val_ratio=0.15):
    """
    데이터를 정규화하고, 슬라이딩 윈도우를 적용하며, 학습/검증/테스트 세트로 분할합니다.
    """
    print(f"\n데이터 전처리 시작... (timesteps={timesteps})")

    # Min-Max Scaling (0-1 범위로 정규화)
    scaler = MinMaxScaler(feature_range=(0, 1))
    scaled_data = scaler.fit_transform(df)
    print("데이터 정규화 완료.")

    # 슬라이딩 윈도우를 사용하여 시퀀스 데이터 생성
    X, y = [], []
    for i in range(timesteps, len(scaled_data)):
        X.append(scaled_data[i-timesteps:i, 0])
        y.append(scaled_data[i, 0])
    X, y = np.array(X), np.array(y)
    print(f"슬라이딩 윈도우 (timesteps={timesteps}) 적용 완료. 생성된 시퀀스 수: {len(X)}")

    # 데이터 분할 (학습, 검증, 테스트)
    total_samples = len(X)
    train_size = int(total_samples * train_ratio)
    val_size = int(total_samples * val_ratio)
    test_size = total_samples - train_size - val_size

    X_train, y_train = X[:train_size], y[:train_size]
    X_val, y_val = X[train_size:train_size + val_size], y[train_size:train_size + val_size]
    X_test, y_test = X[train_size + val_size:], y[train_size + val_size:]

    print(f"학습 세트: {len(X_train)} 시퀀스")
    print(f"검증 세트: {len(X_val)} 시퀀스")
    print(f"테스트 세트: {len(X_test)} 시퀀스")

    X_train = X_train.reshape(X_train.shape[0], X_train.shape[1], 1)
    X_val = X_val.reshape(X_val.shape[0], X_val.shape[1], 1)
    X_test = X_test.reshape(X_test.shape[0], X_test.shape[1], 1)
    print(f"데이터 형태 재구성 완료. X_train.shape: {X_train.shape}")
    
    return X_train, y_train, X_val, y_val, X_test, y_test, scaler

# --- 3. CNN-BiLSTM 모델 구축 (Building CNN-BiLSTM Model) ---
def build_cnn_bilstm_model(timesteps, features=1):
    """
    논문에 제시된 CNN-BiLSTM 아키텍처를 구축합니다.
    """
    print(f"\nCNN-BiLSTM 모델 구축 시작... (timesteps={timesteps})")
    model = Sequential([
        # Conv1D Layer
        Conv1D(filters=128, kernel_size=3, activation='relu', input_shape=(timesteps, features)),
        # MaxPooling1D Layer
        MaxPooling1D(pool_size=2),
        # Bidirectional LSTM Layer 1
        Bidirectional(LSTM(units=150, return_sequences=True)),
        # Dropout Layer
        Dropout(0.2),
        # Bidirectional LSTM Layer 2
        Bidirectional(LSTM(units=50, return_sequences=False)),
        # Dense Layer 1
        Dense(units=64, activation='relu'),
        # Dense Layer 2
        Dense(units=32, activation='relu'),
        # Output Layer
        Dense(units=1)
    ])

    # 모델 컴파일
    optimizer = Adam(learning_rate=0.001)
    model.compile(optimizer=optimizer, loss='mse')
    
    print("모델 요약:")
    model.summary()
    print("모델 구축 완료.")
    return model

# --- 4. 모델 훈련 (Training Model) ---
def train_model(model, X_train, y_train, X_val, y_val, epochs=100, batch_size=16, patience=10):
    """
    Early Stopping을 사용하여 모델을 훈련합니다.
    """
    print("\n모델 훈련 시작...")
    early_stopping = EarlyStopping(
        monitor='val_loss',  # 검증 손실을 모니터링
        patience=patience,   # 10 에포크 동안 개선이 없으면 중단
        restore_best_weights=True  # 가장 성능이 좋았던 에포크의 가중치를 복원
    )

    history = model.fit(
        X_train, y_train,
        epochs=epochs,
        batch_size=batch_size,
        validation_data=(X_val, y_val),
        callbacks=[early_stopping],
        verbose=1
    )
    print("모델 훈련 완료.")
    return history

# --- 5. 모델 평가 (Evaluating Model) ---
def evaluate_model(model, X_test, y_test, scaler, df_original_close):
    """
    테스트 세트에서 모델을 평가하고 MAPE, R²를 계산합니다.
    """
    print("\n모델 평가 시작...")
    
    # 예측 수행 (정규화된 값)
    y_pred_scaled = model.predict(X_test)
    y_test_reshaped = y_test.reshape(-1, 1)
    y_pred_reshaped = y_pred_scaled.reshape(-1, 1)

    y_actual = scaler.inverse_transform(y_test_reshaped)
    y_predicted = scaler.inverse_transform(y_pred_reshaped)
    
    # 평가 지표 계산
    mape = mean_absolute_percentage_error(y_actual, y_predicted) * 100
    r2 = r2_score(y_actual, y_predicted)

    print(f"MAPE: {mape:.4f}%")
    print(f"R²: {r2:.4f}")

    print("모델 평가 완료.")
    return y_actual, y_predicted, mape, r2

# --- 내일 가격 예측 ---
def predict_next_day_price(model, df, scaler, timesteps):
    """
    최근 timesteps만큼의 데이터를 사용하여 내일 가격을 예측합니다.
    """
    # 최근 timesteps개의 데이터 가져오기
    recent_data = df.iloc[-timesteps:].values
    recent_scaled = scaler.transform(recent_data)
    recent_scaled = recent_scaled.reshape(1, timesteps, 1)
    
    # 예측 수행
    next_day_scaled = model.predict(recent_scaled)
    next_day_price = scaler.inverse_transform(next_day_scaled.reshape(-1, 1))
    
    return next_day_price[0][0]

# --- 메인 실행 로직  ---
if __name__ == "__main__":
    # 설정 파라미터
    START_DATE = "2020-01-01"
    END_DATE = "2025-09-17"
    ETH_TICKER = "ETH-USD"
    TRAIN_RATIO = 0.7
    VAL_RATIO = 0.15
    EPOCHS = 100
    BATCH_SIZE = 16
    EARLY_STOPPING_PATIENCE = 10

    # 1. 데이터 획득
    df_ethereum = get_ethereum_data(START_DATE, END_DATE, ETH_TICKER)
    if df_ethereum.empty:
        print("데이터를 성공적으로 다운로드하지 못하여 프로그램을 종료합니다.")
        exit()

    # 결과 저장용 변수들
    results = []
    best_r2 = -1
    best_mape = float('inf')
    best_timesteps = 1
    best_next_day_price = 0

    print("\n" + "="*80)
    print("TIMESTEP 최적화 시작 (1~100)")
    print("="*80)

    # timestep을 1부터 100까지 반복
    for TIMESTEPS in range(1, 101):
        try:
            print(f"\n{'='*50}")
            print(f"TIMESTEPS = {TIMESTEPS}")
            print(f"{'='*50}")
            
            # 2. 데이터 전처리
            X_train, y_train, X_val, y_val, X_test, y_test, scaler = preprocess_data(
                df_ethereum, 
                timesteps=TIMESTEPS, 
                train_ratio=TRAIN_RATIO, 
                val_ratio=VAL_RATIO
            )

            # 3. CNN-BiLSTM 모델 구축
            model = build_cnn_bilstm_model(timesteps=TIMESTEPS, features=X_train.shape[2])

            # 4. 모델 훈련
            history = train_model(
                model, 
                X_train, y_train, 
                X_val, y_val, 
                epochs=EPOCHS, 
                batch_size=BATCH_SIZE, 
                patience=EARLY_STOPPING_PATIENCE
            )

            # 5. 모델 평가
            y_actual, y_predicted, mape_result, r2_result = evaluate_model(model, X_test, y_test, scaler, df_ethereum)

            # 6. 내일 가격 예측
            next_day_price = predict_next_day_price(model, df_ethereum, scaler, TIMESTEPS)

            # 결과 저장
            result = {
                'timesteps': TIMESTEPS,
                'mape': mape_result,
                'r2': r2_result,
                'next_day_price': next_day_price
            }
            results.append(result)

            print(f"\n--- TIMESTEPS {TIMESTEPS} 결과 ---")
            print(f"MAPE: {mape_result:.4f}%")
            print(f"R²: {r2_result:.4f}")
            print(f"내일 예상 가격: ${next_day_price:.2f}")

            if r2_result > best_r2:
                best_r2 = r2_result
                best_mape = mape_result
                best_timesteps = TIMESTEPS
                best_next_day_price = next_day_price

        except Exception as e:
            print(f"TIMESTEPS {TIMESTEPS}에서 오류 발생: {e}")
            continue

    # 최종 결과 출력
    print("\n" + "="*80)
    print("최적화 완료 - 전체 결과 요약")
    print("="*80)

    results_sorted = sorted(results, key=lambda x: x['r2'], reverse=True)
    
    print(f"{'순위':<4} {'Timesteps':<10} {'R²':<10} {'MAPE(%)':<10} {'내일가격($)':<12}")
    print("-" * 60)
    for i, result in enumerate(results_sorted[:10], 1):
        print(f"{i:<4} {result['timesteps']:<10} {result['r2']:<10.4f} {result['mape']:<10.4f} {result['next_day_price']:<12.2f}")

    print(f"\n{'='*80}")
    print(f"{'='*80}")
    print(f"최적 TIMESTEPS: {best_timesteps}")
    print(f"최고 R²: {best_r2:.4f}")
    print(f" MAPE: {best_mape:.4f}%")
    print(f"내일 예상 이더리움 가격: ${best_next_day_price:.2f}")
    
    print(f"최적 결과 MAPE: {best_mape:.4f}%")
    print(f"최적 결과 R²: {best_r2:.4f}")

2025-09-17 16:42:09.576172: I external/local_xla/xla/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.
2025-09-17 16:42:09.631865: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-09-17 16:42:10.910731: I external/local_xla/xla/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.


이더리움 데이터 다운로드 중: 2020-01-01 ~ 2025-09-17


/tmp/ipykernel_3730135/4140164304.py:20: FutureWarning: YF.download() has changed argument auto_adjust default to True
  data = yf.download(ticker, start=start_date, end=end_date)
[*********************100%***********************]  1 of 1 completed
/raid/invigoworks/anaconda3/lib/python3.10/site-packages/keras/src/layers/convolutional/base_conv.py:113: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)
E0000 00:00:1758094933.401182 3730135 cuda_executor.cc:1309] INTERNAL: CUDA Runtime error: Failed call to cudaGetRuntimeVersion: Error loading CUDA libraries. GPU will not be used.: Error loading CUDA libraries. GPU will not be used.
W0000 00:00:1758094933.464998 3730135 gpu_device.cc:2342] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are inst

데이터 다운로드 완료.

TIMESTEP 최적화 시작 (1~100)

TIMESTEPS = 1

데이터 전처리 시작... (timesteps=1)
데이터 정규화 완료.
슬라이딩 윈도우 (timesteps=1) 적용 완료. 생성된 시퀀스 수: 2084
학습 세트: 1458 시퀀스
검증 세트: 312 시퀀스
테스트 세트: 314 시퀀스
데이터 형태 재구성 완료. X_train.shape: (1458, 1, 1)

CNN-BiLSTM 모델 구축 시작... (timesteps=1)
TIMESTEPS 1에서 오류 발생: Computed output size would be negative. Received `inputs shape=(None, 1, 1)`, `kernel shape=(3, 1, 128)`, `dilation_rate=[1]`.

TIMESTEPS = 2

데이터 전처리 시작... (timesteps=2)
데이터 정규화 완료.
슬라이딩 윈도우 (timesteps=2) 적용 완료. 생성된 시퀀스 수: 2083
학습 세트: 1458 시퀀스
검증 세트: 312 시퀀스
테스트 세트: 313 시퀀스
데이터 형태 재구성 완료. X_train.shape: (1458, 2, 1)

CNN-BiLSTM 모델 구축 시작... (timesteps=2)
모델 요약:


/raid/invigoworks/anaconda3/lib/python3.10/site-packages/keras/src/layers/convolutional/base_conv.py:113: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv1d_99 (Conv1D)              │ (None, 98, 128)        │           512 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling1d_99 (MaxPooling1D) │ (None, 49, 128)        │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ bidirectional_198               │ (None, 49, 300)        │       334,800 │
│ (Bidirectional)                 │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_99 (Dropout)            │ (None, 49, 300)        │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ bidirectional_199               │ (None, 100)            │       140,400 │
│ (Bidirectional)                 │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_297 (Dense)               │ (None, 64)             │         6,464 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_298 (Dense)               │ (None, 32)             │         2,080 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_299 (Dense)               │ (None, 1)              │            33 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 484,289 (1.85 MB)

 Trainable params: 484,289 (1.85 MB)

 Non-trainable params: 0 (0.00 B)

모델 구축 완료.

모델 훈련 시작...
Epoch 1/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 13s 104ms/step - loss: 0.0098 - val_loss: 0.0062
Epoch 2/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 98ms/step - loss: 0.0032 - val_loss: 0.0024
Epoch 3/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 99ms/step - loss: 0.0021 - val_loss: 0.0023
Epoch 4/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 99ms/step - loss: 0.0020 - val_loss: 0.0018
Epoch 5/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 98ms/step - loss: 0.0014 - val_loss: 0.0023
Epoch 6/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 99ms/step - loss: 0.0013 - val_loss: 0.0027
Epoch 7/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 99ms/step - loss: 0.0013 - val_loss: 0.0011
Epoch 8/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 98ms/step - loss: 0.0011 - val_loss: 0.0018
Epoch 9/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 9s 99ms/step - loss: 9.6985e-04 - val_loss: 0.0010
Epoch 10/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 100ms/step - loss: 0.0010 - val_loss: 7.3834e-04
Epoch 11/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 100ms/step - loss: 8.0766e-04 - val_loss: 9.1944e-04


In [2]:
import pandas as pd
import numpy as np
import yfinance as yf
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_percentage_error, r2_score
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv1D, MaxPooling1D, Bidirectional, LSTM, Dense, Dropout
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping
import matplotlib.pyplot as plt
import datetime

# --- 1. 데이터 획득  ---
def get_ethereum_data(start_date="2020-01-01", end_date="2025-09-17", ticker="ETH-USD"):
    """
    Yahoo Finance에서 이더리움 일일 종가 데이터를 다운로드합니다.
    """
    print(f"이더리움 데이터 다운로드 중: {start_date} ~ {end_date}")
    try:
        data = yf.download(ticker, start=start_date, end=end_date)
        if data.empty:
            raise ValueError("다운로드된 데이터가 없습니다. 날짜 범위 또는 티커를 확인하세요.")
        df_close = data[['Close']]
        print("데이터 다운로드 완료.")
        return df_close
    except Exception as e:
        print(f"데이터 다운로드 중 오류 발생: {e}")
        return pd.DataFrame()

# --- 2. 데이터 전처리 ---
def preprocess_data(df, timesteps=16, train_ratio=0.7, val_ratio=0.15):
    """
    데이터를 정규화하고, 슬라이딩 윈도우를 적용하며, 학습/검증/테스트 세트로 분할합니다.
    """
    print(f"\n데이터 전처리 시작... (timesteps={timesteps})")

    # Min-Max Scaling (0-1 범위로 정규화)
    scaler = MinMaxScaler(feature_range=(0, 1))
    scaled_data = scaler.fit_transform(df)
    print("데이터 정규화 완료.")

    # 슬라이딩 윈도우를 사용하여 시퀀스 데이터 생성
    X, y = [], []
    for i in range(timesteps, len(scaled_data)):
        X.append(scaled_data[i-timesteps:i, 0])
        y.append(scaled_data[i, 0])
    X, y = np.array(X), np.array(y)
    print(f"슬라이딩 윈도우 (timesteps={timesteps}) 적용 완료. 생성된 시퀀스 수: {len(X)}")

    # 데이터 분할 (학습, 검증, 테스트)
    total_samples = len(X)
    train_size = int(total_samples * train_ratio)
    val_size = int(total_samples * val_ratio)
    test_size = total_samples - train_size - val_size

    X_train, y_train = X[:train_size], y[:train_size]
    X_val, y_val = X[train_size:train_size + val_size], y[train_size:train_size + val_size]
    X_test, y_test = X[train_size + val_size:], y[train_size + val_size:]

    print(f"학습 세트: {len(X_train)} 시퀀스")
    print(f"검증 세트: {len(X_val)} 시퀀스")
    print(f"테스트 세트: {len(X_test)} 시퀀스")

    X_train = X_train.reshape(X_train.shape[0], X_train.shape[1], 1)
    X_val = X_val.reshape(X_val.shape[0], X_val.shape[1], 1)
    X_test = X_test.reshape(X_test.shape[0], X_test.shape[1], 1)
    print(f"데이터 형태 재구성 완료. X_train.shape: {X_train.shape}")
    
    return X_train, y_train, X_val, y_val, X_test, y_test, scaler

# --- 3. CNN-BiLSTM 모델 구축 (Building CNN-BiLSTM Model) ---
def build_cnn_bilstm_model(timesteps, features=1):
    """
    논문에 제시된 CNN-BiLSTM 아키텍처를 구축합니다.
    """
    print(f"\nCNN-BiLSTM 모델 구축 시작... (timesteps={timesteps})")
    model = Sequential([
        # Conv1D Layer
        Conv1D(filters=128, kernel_size=3, activation='relu', input_shape=(timesteps, features)),
        # MaxPooling1D Layer
        MaxPooling1D(pool_size=2),
        # Bidirectional LSTM Layer 1
        Bidirectional(LSTM(units=150, return_sequences=True)),
        # Dropout Layer
        Dropout(0.2),
        # Bidirectional LSTM Layer 2
        Bidirectional(LSTM(units=50, return_sequences=False)),
        # Dense Layer 1
        Dense(units=64, activation='relu'),
        # Dense Layer 2
        Dense(units=32, activation='relu'),
        # Output Layer
        Dense(units=1)
    ])

    # 모델 컴파일
    optimizer = Adam(learning_rate=0.001)
    model.compile(optimizer=optimizer, loss='mse')
    
    print("모델 요약:")
    model.summary()
    print("모델 구축 완료.")
    return model

# --- 4. 모델 훈련 (Training Model) ---
def train_model(model, X_train, y_train, X_val, y_val, epochs=100, batch_size=16, patience=10):
    """
    Early Stopping을 사용하여 모델을 훈련합니다.
    """
    print("\n모델 훈련 시작...")
    early_stopping = EarlyStopping(
        monitor='val_loss',  # 검증 손실을 모니터링
        patience=patience,   # 10 에포크 동안 개선이 없으면 중단
        restore_best_weights=True  # 가장 성능이 좋았던 에포크의 가중치를 복원
    )

    history = model.fit(
        X_train, y_train,
        epochs=epochs,
        batch_size=batch_size,
        validation_data=(X_val, y_val),
        callbacks=[early_stopping],
        verbose=1
    )
    print("모델 훈련 완료.")
    return history

# --- 5. 모델 평가 (Evaluating Model) ---
def evaluate_model(model, X_test, y_test, scaler, df_original_close):
    """
    테스트 세트에서 모델을 평가하고 MAPE, R²를 계산합니다.
    """
    print("\n모델 평가 시작...")
    
    # 예측 수행 (정규화된 값)
    y_pred_scaled = model.predict(X_test)
    y_test_reshaped = y_test.reshape(-1, 1)
    y_pred_reshaped = y_pred_scaled.reshape(-1, 1)

    y_actual = scaler.inverse_transform(y_test_reshaped)
    y_predicted = scaler.inverse_transform(y_pred_reshaped)
    
    # 평가 지표 계산
    mape = mean_absolute_percentage_error(y_actual, y_predicted) * 100
    r2 = r2_score(y_actual, y_predicted)

    print(f"MAPE: {mape:.4f}%")
    print(f"R²: {r2:.4f}")

    print("모델 평가 완료.")
    return y_actual, y_predicted, mape, r2

# --- 내일 가격 예측 ---
def predict_next_day_price(model, df, scaler, timesteps):
    """
    최근 timesteps만큼의 데이터를 사용하여 내일 가격을 예측합니다.
    """
    # 최근 timesteps개의 데이터 가져오기
    recent_data = df.iloc[-timesteps:].values
    recent_scaled = scaler.transform(recent_data)
    recent_scaled = recent_scaled.reshape(1, timesteps, 1)
    
    # 예측 수행
    next_day_scaled = model.predict(recent_scaled)
    next_day_price = scaler.inverse_transform(next_day_scaled.reshape(-1, 1))
    
    return next_day_price[0][0]

# --- 메인 실행 로직  ---
if __name__ == "__main__":
    # 설정 파라미터
    START_DATE = "2020-01-01"
    END_DATE = "2025-09-17"
    ETH_TICKER = "ETH-USD"
    TRAIN_RATIO = 0.7
    VAL_RATIO = 0.15
    EPOCHS = 100
    BATCH_SIZE = 16
    EARLY_STOPPING_PATIENCE = 10

    # 1. 데이터 획득
    df_ethereum = get_ethereum_data(START_DATE, END_DATE, ETH_TICKER)
    if df_ethereum.empty:
        print("데이터를 성공적으로 다운로드하지 못하여 프로그램을 종료합니다.")
        exit()

    # 결과 저장용 변수들
    results = []
    best_r2 = -1
    best_mape = float('inf')
    best_timesteps = 1
    best_next_day_price = 0

    print("\n" + "="*80)
    print("TIMESTEP 최적화 시작 (1~100)")
    print("="*80)

    # timestep을 1부터 100까지 반복
    for TIMESTEPS in range(1, 101):
        try:
            print(f"\n{'='*50}")
            print(f"TIMESTEPS = {TIMESTEPS}")
            print(f"{'='*50}")
            
            # 2. 데이터 전처리
            X_train, y_train, X_val, y_val, X_test, y_test, scaler = preprocess_data(
                df_ethereum, 
                timesteps=TIMESTEPS, 
                train_ratio=TRAIN_RATIO, 
                val_ratio=VAL_RATIO
            )

            # 3. CNN-BiLSTM 모델 구축
            model = build_cnn_bilstm_model(timesteps=TIMESTEPS, features=X_train.shape[2])

            # 4. 모델 훈련
            history = train_model(
                model, 
                X_train, y_train, 
                X_val, y_val, 
                epochs=EPOCHS, 
                batch_size=BATCH_SIZE, 
                patience=EARLY_STOPPING_PATIENCE
            )

            # 5. 모델 평가
            y_actual, y_predicted, mape_result, r2_result = evaluate_model(model, X_test, y_test, scaler, df_ethereum)

            # 6. 내일 가격 예측
            next_day_price = predict_next_day_price(model, df_ethereum, scaler, TIMESTEPS)

            # 결과 저장
            result = {
                'timesteps': TIMESTEPS,
                'mape': mape_result,
                'r2': r2_result,
                'next_day_price': next_day_price
            }
            results.append(result)

            print(f"\n--- TIMESTEPS {TIMESTEPS} 결과 ---")
            print(f"MAPE: {mape_result:.4f}%")
            print(f"R²: {r2_result:.4f}")
            print(f"내일 예상 가격: ${next_day_price:.2f}")

            if r2_result > best_r2:
                best_r2 = r2_result
                best_mape = mape_result
                best_timesteps = TIMESTEPS
                best_next_day_price = next_day_price

        except Exception as e:
            print(f"TIMESTEPS {TIMESTEPS}에서 오류 발생: {e}")
            continue

    # 최종 결과 출력
    print("\n" + "="*80)
    print("최적화 완료 - 전체 결과 요약")
    print("="*80)

    results_sorted = sorted(results, key=lambda x: x['r2'], reverse=True)
    
    print(f"{'순위':<4} {'Timesteps':<10} {'R²':<10} {'MAPE(%)':<10} {'내일가격($)':<12}")
    print("-" * 60)
    for i, result in enumerate(results_sorted[:10], 1):
        print(f"{i:<4} {result['timesteps']:<10} {result['r2']:<10.4f} {result['mape']:<10.4f} {result['next_day_price']:<12.2f}")

    print(f"\n{'='*80}")
    print(f"{'='*80}")
    print(f"최적 TIMESTEPS: {best_timesteps}")
    print(f"최고 R²: {best_r2:.4f}")
    print(f" MAPE: {best_mape:.4f}%")
    print(f"내일 예상 이더리움 가격: ${best_next_day_price:.2f}")
    
    print(f"최적 결과 MAPE: {best_mape:.4f}%")
    print(f"최적 결과 R²: {best_r2:.4f}")

2025-09-17 16:42:09.576172: I external/local_xla/xla/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.
2025-09-17 16:42:09.631865: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-09-17 16:42:10.910731: I external/local_xla/xla/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.


이더리움 데이터 다운로드 중: 2020-01-01 ~ 2025-09-17


/tmp/ipykernel_3730135/4140164304.py:20: FutureWarning: YF.download() has changed argument auto_adjust default to True
  data = yf.download(ticker, start=start_date, end=end_date)
[*********************100%***********************]  1 of 1 completed
/raid/invigoworks/anaconda3/lib/python3.10/site-packages/keras/src/layers/convolutional/base_conv.py:113: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)
E0000 00:00:1758094933.401182 3730135 cuda_executor.cc:1309] INTERNAL: CUDA Runtime error: Failed call to cudaGetRuntimeVersion: Error loading CUDA libraries. GPU will not be used.: Error loading CUDA libraries. GPU will not be used.
W0000 00:00:1758094933.464998 3730135 gpu_device.cc:2342] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are inst

데이터 다운로드 완료.

TIMESTEP 최적화 시작 (1~100)

TIMESTEPS = 1

데이터 전처리 시작... (timesteps=1)
데이터 정규화 완료.
슬라이딩 윈도우 (timesteps=1) 적용 완료. 생성된 시퀀스 수: 2084
학습 세트: 1458 시퀀스
검증 세트: 312 시퀀스
테스트 세트: 314 시퀀스
데이터 형태 재구성 완료. X_train.shape: (1458, 1, 1)

CNN-BiLSTM 모델 구축 시작... (timesteps=1)
TIMESTEPS 1에서 오류 발생: Computed output size would be negative. Received `inputs shape=(None, 1, 1)`, `kernel shape=(3, 1, 128)`, `dilation_rate=[1]`.

TIMESTEPS = 2

데이터 전처리 시작... (timesteps=2)
데이터 정규화 완료.
슬라이딩 윈도우 (timesteps=2) 적용 완료. 생성된 시퀀스 수: 2083
학습 세트: 1458 시퀀스
검증 세트: 312 시퀀스
테스트 세트: 313 시퀀스
데이터 형태 재구성 완료. X_train.shape: (1458, 2, 1)

CNN-BiLSTM 모델 구축 시작... (timesteps=2)
모델 요약:


/raid/invigoworks/anaconda3/lib/python3.10/site-packages/keras/src/layers/convolutional/base_conv.py:113: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv1d_99 (Conv1D)              │ (None, 98, 128)        │           512 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling1d_99 (MaxPooling1D) │ (None, 49, 128)        │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ bidirectional_198               │ (None, 49, 300)        │       334,800 │
│ (Bidirectional)                 │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_99 (Dropout)            │ (None, 49, 300)        │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ bidirectional_199               │ (None, 100)            │       140,400 │
│ (Bidirectional)                 │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_297 (Dense)               │ (None, 64)             │         6,464 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_298 (Dense)               │ (None, 32)             │         2,080 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_299 (Dense)               │ (None, 1)              │            33 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 484,289 (1.85 MB)

 Trainable params: 484,289 (1.85 MB)

 Non-trainable params: 0 (0.00 B)

모델 구축 완료.

모델 훈련 시작...
Epoch 1/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 13s 104ms/step - loss: 0.0098 - val_loss: 0.0062
Epoch 2/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 98ms/step - loss: 0.0032 - val_loss: 0.0024
Epoch 3/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 99ms/step - loss: 0.0021 - val_loss: 0.0023
Epoch 4/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 99ms/step - loss: 0.0020 - val_loss: 0.0018
Epoch 5/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 98ms/step - loss: 0.0014 - val_loss: 0.0023
Epoch 6/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 99ms/step - loss: 0.0013 - val_loss: 0.0027
Epoch 7/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 99ms/step - loss: 0.0013 - val_loss: 0.0011
Epoch 8/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 98ms/step - loss: 0.0011 - val_loss: 0.0018
Epoch 9/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 9s 99ms/step - loss: 9.6985e-04 - val_loss: 0.0010
Epoch 10/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 100ms/step - loss: 0.0010 - val_loss: 7.3834e-04
Epoch 11/100
87/87 ━━━━━━━━━━━━━━━━━━━━ 10s 100ms/step - loss: 8.0766e-04 - val_loss: 9.1944e-04
